In [1]:
%matplotlib inline

import glob
import pandas as pd
import yaml
import numpy as np
import cv2
import time
from skimage import exposure
from skimage import feature
import matplotlib.pyplot as plt

In [2]:
prefix = 'C:\\Users\\rafae\\Desktop\\Coleta\\faces\\training_*.csv'

In [3]:
import yaml
skip_lines = 3
def read_yaml_depth(file):
    file_yaml = file.replace('bmp', 'yaml')
    print(file_yaml)
    with open(file_yaml) as infile:
        for i in range(skip_lines):
            _ = infile.readline()
        data = yaml.load(infile)
    return np.reshape(data['data'], (data['rows'], data['cols']))

In [4]:
def show_hog_img(img, hog_img):
    for i in range(4):
        hog_img[i] = exposure.rescale_intensity(hog_img[i], out_range=(0, 255))
        hog_img[i] = hog_img[i].astype("uint8")

    img_concat = np.concatenate((img[0], img[1],img[2],img[3]), axis = 1)
    img_hog_concat = np.concatenate((img[0], hog_img[1],hog_img[2],hog_img[3]), axis = 1)
    
    img_total = np.concatenate((img_concat, img_hog_concat), axis = 0)
    
    fig, ax = plt.subplots(nrows=1, ncols=4)
    for i in range(4):
        plt.subplot(1, 4, i+1)
        plt.hist(hog_img[i])
    plt.show()

    cv2.imshow("HOG Image", img_total)
    cv2.waitKey(0)
    cv2.destroyAllWindows()

In [5]:
show_hog_image = False

def calculate_hog(row):
    tic = time.clock()
    
    # improvement agrupar
    #dep = cv2.imread(row['depfile_path'],0)
    dep = read_yaml_depth(row['depfile_path'])
    dep = dep[row['depxs']:row['depxe'],row['depys']:row['depye']]
    dep = (dep - dep.mean()) / dep.std()
    (H_dep, dep_hog) = feature.hog(dep, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2,2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    print(dep.shape, dep_hog.shape, H_dep.shape)
    
    ir1 = cv2.imread(row['ir1file_path'],0)
    ir1 = ir1[row['ir1xs']:row['ir1xe'],row['ir1ys']:row['ir1ye']]
    (H_ir1, ir1_hog) = feature.hog(ir1, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2, 2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    #print(ir1.shape, ir1_hog.shape, H_ir1.shape)
    
    ir2 = cv2.imread(row['ir2file_path'],0)
    ir2 = ir2[row['ir2xs']:row['ir2xe'],row['ir2ys']:row['ir2ye']]
    (H_ir2, ir2_hog) = feature.hog(ir2, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2, 2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    #print(ir2.shape, ir2_hog.shape, H_ir2.shape)
    
    rgb = cv2.imread(row['rgbfile_path'],0)
    rgb = rgb[row['rgbxs']:row['rgbxe'],row['rgbys']:row['rgbye']]
    (H_rgb, rgb_hog) = feature.hog(rgb, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2, 2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    #print(rgb.shape, rgb_hog.shape, H_rgb.shape)
    
    data = [row['class'], row['person']]
    data.extend(H_dep)
    data.extend(H_ir1)
    data.extend(H_ir2)
    data.extend(H_rgb)
    
    data_hog.append(data)
    
    if show_hog_image == True:
        show_hog_img([dep,ir1,ir2,rgb], [dep_hog, ir1_hog, ir2_hog, rgb_hog])
        
    print(ds.shape, len(data_hog), row['depfile_path'], (time.clock() - tic))

In [40]:
# import the necessary packages
from skimage import feature
import numpy as np
 
class LocalBinaryPatterns:
    def __init__(self, numPoints, radius):
        # store the number of points and radius
        self.numPoints = numPoints
        self.radius = radius
 
    def describe(self, image, eps=1e-7):
        # compute the Local Binary Pattern representation
        # of the image, and then use the LBP representation
        # to build the histogram of patterns
        lbp = feature.local_binary_pattern(image, self.numPoints,
            self.radius, method="uniform")
        n_bins = self.numPoints*(self.numPoints-1)+3
        (hist, _) = np.histogram(lbp.ravel(),
            bins=n_bins,range=(0, n_bins))
        # normalize the histogram
        #hist = hist.astype("float")
        #hist /= (hist.sum() + eps)
        #plt.hist(hist)
        #plt.show()
        # return the histogram of Local Binary Patterns
        return (hist, lbp)

In [41]:
show_lbp_image = False

def calculate_lbp(row):
    tic = time.clock()
    desc = LocalBinaryPatterns(8, 1)
    
    # improvement agrupar
    depr = read_yaml_depth(row['depfile_path'])
    depr = depr[row['depxs']:row['depxe'],row['depys']:row['depye']]
    depr = (depr - depr.mean()) / depr.std() #equalize image
    #(H_dep, dep_hog) = feature.hog(dep, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2,2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    (H_depr_temp, depr_hog) = desc.describe(depr)
    H_depr = []
    H_depr.extend(H_depr_temp)
    #print(depr.shape)
    for height in range(0,97, 8):
        for width in range(0,81, 8):
            print(height,height+8,width,width+8)
            (H_depr_temp, depr_hog) = desc.describe(depr[height:height+8,width:width+8])
            H_depr.extend(H_depr_temp)
    #print(len(H_depr), H_depr)
    #dep = (dep - dep.mean()) / dep.std()
    #dep = cv2.imread(row['depfile_path'],0)    
    #dep = dep[row['depxs']:row['depxe'],row['depys']:row['depye']]
    
    #(H_dep, dep_hog) = feature.hog(dep, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2,2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    #(H_dep, dep_hog) = desc.describe(dep)
    #print(H_dep.shape)
    
    ir1 = cv2.imread(row['ir1file_path'],0)
    ir1 = ir1[row['ir1xs']:row['ir1xe'],row['ir1ys']:row['ir1ye']]
    #(H_ir1, ir1_hog) = feature.hog(ir1, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2, 2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    (H_ir1, ir1_hog) = desc.describe(ir1)
    print(H_ir1.shape)
    #print(ir1.shape, ir1_hog.shape, H_ir1.shape)
    
    ir2 = cv2.imread(row['ir2file_path'],0)
    ir2 = ir2[row['ir2xs']:row['ir2xe'],row['ir2ys']:row['ir2ye']]
    #(H_ir2, ir2_hog) = feature.hog(ir2, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2, 2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    (H_ir2, ir2_hog) = desc.describe(ir2)
    print(H_ir2.shape)
    #print(ir2.shape, ir2_hog.shape, H_ir2.shape)
    
    rgb = cv2.imread(row['rgbfile_path'],0)
    rgb = rgb[row['rgbxs']:row['rgbxe'],row['rgbys']:row['rgbye']]
    #(H_rgb, rgb_hog) = feature.hog(rgb, orientations=9, pixels_per_cell=(8, 8),cells_per_block=(2, 2), transform_sqrt=True, visualise=True, block_norm='L2-Hys')
    (H_rgb, rgb_hog) = desc.describe(rgb)
    print(H_rgb.shape)
    #print(rgb.shape, rgb_hog.shape, H_rgb.shape)
    
    data = [row['class'], row['person']]
    data.extend(H_depr)
    #data.extend(H_dep)
    data.extend(H_ir1)
    data.extend(H_ir2)
    data.extend(H_rgb)
    
    data_hog.append(data)
    
    if show_lbp_image == True:
        show_hog_img([dep,ir1,ir2,rgb], [dep_hog, ir1_hog, ir2_hog, rgb_hog])
        
    print(ds.shape, len(data_hog), row['depfile_path'], (time.clock() - tic))

In [42]:
files_list = glob.glob(prefix)
print(len(files_list))

518


In [54]:
test = files_list[335:]
print(test[0], len(test))

C:\Users\rafae\Desktop\Coleta\faces\training_p024_14.csv 183


In [55]:
feature_desc = 'lbp'

for f in test:
#f = files_list[50]
    ds = pd.read_csv(f, header=0)
    print(ds.shape, f)

    data_hog = []
    tic = time.clock()
    savefile = False
    for index, row in ds.iterrows():
        if feature_desc == 'lbp':
            calculate_lbp(row)
        else:
            calculate_hog(row)
    print(time.clock() - tic)

    if len(data_hog) > 0:
        print(len(data_hog[0]))
        # save file
        df = pd.DataFrame(data_hog)
        filename = 'features_n_{:s}_{:s}_{:d}.csv'.format(feature_desc, ds['person'][0],ds['class'][0])
        df.to_csv(filename, index=False, encoding='utf-8')

(15, 22) C:\Users\rafae\Desktop\Coleta\faces\training_p024_14.csv
E:\MestradoData\p024\24_14_depth_11.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
56 64 0 8
56 64 8 16
56

(59,)
(59,)
(59,)
(15, 22) 5 E:\MestradoData\p024\24_14_depth_51.bmp 22.63151476027997
E:\MestradoData\p024\24_14_depth_61.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
56

72 80 80 88
80 88 0 8
80 88 8 16
80 88 16 24
80 88 24 32
80 88 32 40
80 88 40 48
80 88 48 56
80 88 56 64
80 88 64 72
80 88 72 80
80 88 80 88
88 96 0 8
88 96 8 16
88 96 16 24
88 96 24 32
88 96 32 40
88 96 40 48
88 96 48 56
88 96 56 64
88 96 64 72
88 96 72 80
88 96 80 88
96 104 0 8
96 104 8 16
96 104 16 24
96 104 24 32
96 104 32 40
96 104 40 48
96 104 48 56
96 104 56 64
96 104 64 72
96 104 72 80
96 104 80 88
(59,)
(59,)
(59,)
(15, 22) 10 E:\MestradoData\p024\24_14_depth_101.bmp 21.861276949115563
E:\MestradoData\p024\24_14_depth_111.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72

40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
56 64 0 8
56 64 8 16
56 64 16 24
56 64 24 32
56 64 32 40
56 64 40 48
56 64 48 56
56 64 56 64
56 64 64 72
56 64 72 80
56 64 80 88
64 72 0 8
64 72 8 16
64 72 16 24
64 72 24 32
64 72 32 40
64 72 40 48
64 72 48 56
64 72 56 64
64 72 64 72
64 72 72 80
64 72 80 88
72 80 0 8
72 80 8 16
72 80 16 24
72 80 24 32
72 80 32 40
72 80 40 48
72 80 48 56
72 80 56 64
72 80 64 72
72 80 72 80
72 80 80 88
80 88 0 8
80 88 8 16
80 88 16 24
80 88 24 32
80 88 32 40
80 88 40 48
80 88 48 56
80 88 56 64
80 88 64 72
80 88 72 80
80 88 80 88
88 96 0 8
88 96 8 16
88 96 16 24
88 96 24 32
88 96 32 40
88 96 40 48
88 96 48 56
88 96 56 64
88 96 64 72
88 96 72 80
88 96 80 88
96 104 0 8
96 104 8 16
96 104 16 24
96 104 24 32
96 104 32 40
96 104 40 48
96 104 48 56
96 104 56 64
96 104 64 72
96 104 72 80
96 104 80 88
(59,)
(59,)
(59,)
(15, 22) 15 E:\MestradoData\p024\24_14_depth

0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
56 64 0 8
56 64 8 16
56 64 16 24
56 64 24 32
56 64 32 40
56 64 40 48
56 64 48 56
56 64 56 64
56 64 64 72
56 64 72 80
56 64 80 88
6

...

(59,)
(59,)
(59,)
(15, 22) 7 E:\MestradoData\p033\33_8_depth_101.bmp 15.640413123634062
E:\MestradoData\p033\33_8_depth_111.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
5

64 72 40 48
64 72 48 56
64 72 56 64
64 72 64 72
64 72 72 80
64 72 80 88
72 80 0 8
72 80 8 16
72 80 16 24
72 80 24 32
72 80 32 40
72 80 40 48
72 80 48 56
72 80 56 64
72 80 64 72
72 80 72 80
72 80 80 88
80 88 0 8
80 88 8 16
80 88 16 24
80 88 24 32
80 88 32 40
80 88 40 48
80 88 48 56
80 88 56 64
80 88 64 72
80 88 72 80
80 88 80 88
88 96 0 8
88 96 8 16
88 96 16 24
88 96 24 32
88 96 32 40
88 96 40 48
88 96 48 56
88 96 56 64
88 96 64 72
88 96 72 80
88 96 80 88
96 104 0 8
96 104 8 16
96 104 16 24
96 104 24 32
96 104 32 40
96 104 40 48
96 104 48 56
96 104 56 64
96 104 64 72
96 104 72 80
96 104 80 88
(59,)
(59,)
(59,)
(15, 22) 12 E:\MestradoData\p033\33_8_depth_151.bmp 15.721378590518725
E:\MestradoData\p033\33_8_depth_161.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
1

(59,)
(59,)
(59,)
(15, 22) 2 E:\MestradoData\p033\33_9_depth_21.bmp 15.906037012508023
E:\MestradoData\p033\33_9_depth_31.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
56 

(59,)
(59,)
(59,)
(15, 22) 7 E:\MestradoData\p033\33_9_depth_71.bmp 14.81587649116409
E:\MestradoData\p033\33_9_depth_81.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40 48
48 56 48 56
48 56 56 64
48 56 64 72
48 56 72 80
48 56 80 88
56 6

96 104 48 56
96 104 56 64
96 104 64 72
96 104 72 80
96 104 80 88
(59,)
(59,)
(59,)
(15, 22) 12 E:\MestradoData\p033\33_9_depth_121.bmp 14.75990537488542
E:\MestradoData\p033\33_9_depth_131.yaml
0 8 0 8
0 8 8 16
0 8 16 24
0 8 24 32
0 8 32 40
0 8 40 48
0 8 48 56
0 8 56 64
0 8 64 72
0 8 72 80
0 8 80 88
8 16 0 8
8 16 8 16
8 16 16 24
8 16 24 32
8 16 32 40
8 16 40 48
8 16 48 56
8 16 56 64
8 16 64 72
8 16 72 80
8 16 80 88
16 24 0 8
16 24 8 16
16 24 16 24
16 24 24 32
16 24 32 40
16 24 40 48
16 24 48 56
16 24 56 64
16 24 64 72
16 24 72 80
16 24 80 88
24 32 0 8
24 32 8 16
24 32 16 24
24 32 24 32
24 32 32 40
24 32 40 48
24 32 48 56
24 32 56 64
24 32 64 72
24 32 72 80
24 32 80 88
32 40 0 8
32 40 8 16
32 40 16 24
32 40 24 32
32 40 32 40
32 40 40 48
32 40 48 56
32 40 56 64
32 40 64 72
32 40 72 80
32 40 80 88
40 48 0 8
40 48 8 16
40 48 16 24
40 48 24 32
40 48 32 40
40 48 40 48
40 48 48 56
40 48 56 64
40 48 64 72
40 48 72 80
40 48 80 88
48 56 0 8
48 56 8 16
48 56 16 24
48 56 24 32
48 56 32 40
48 56 40

In [ ]:
from sklearn.metrics import make_scorer,precision_recall_fscore_support


make_scorer(precision_recall_fscore_support, labels = [1,2,3])

In [ ]:
ds.head()